# Preprocessing for Curb Data

In [2]:
# Enable autoload for just updated files
%load_ext autoreload
%autoreload 2

In [2]:
import sys
import numpy as np
sys.path.append('../../')   # Add parent directory to Python path
from utils.preprocessing import *
from utils.segmentation import *
from utils.visualization import *

# #P1 Cobblestone Road E1-E3

In [7]:
#Missing value and combined data
#Load the E1 Data and handle missing values
df_one= pd.read_csv('../../data/RoadRoughness/Raw/Cobblestone/P1/E1/HandleBar/Accelerometer/Accelerometer.0.csv')  
df_two= pd.read_csv('../../data/RoadRoughness/Raw/Cobblestone/P1/E2/HandleBar/Accelerometer/Accelerometer.0.csv')  
df_three= pd.read_csv('../../data/RoadRoughness/Raw/Cobblestone/P1/E3/HandleBar/Accelerometer/Accelerometer.0.csv')  
df_combined = pd.concat([df_one, df_two, df_three], ignore_index=True)
print(df_combined.isnull().sum())
print(df_combined.shape)

Date         0
NTP          0
GNSS-Time    0
Acc-X        0
Acc-Y        0
Acc-Z        0
dtype: int64
(26296, 6)


In [8]:
df_combined

Date                      NTP  GNSS-Time     Acc-X  \
0      2024-11-18T16:19:50.132  2024-11-18 16:19:49.844         -1 -0.215354   
1      2024-11-18T16:19:50.136  2024-11-18 16:19:49.849         -1 -0.431306   
2      2024-11-18T16:19:50.141  2024-11-18 16:19:49.853         -1 -0.434297   
3      2024-11-18T16:19:50.143  2024-11-18 16:19:49.856         -1 -0.202194   
4      2024-11-18T16:19:50.150  2024-11-18 16:19:49.863         -1 -0.314058   
...                        ...                      ...        ...       ...   
26291  2024-11-18T16:23:31.673  2024-11-18 16:23:31.386         -1 -0.249751   
26292  2024-11-18T16:23:31.677  2024-11-18 16:23:31.390         -1 -0.007478   
26293  2024-11-18T16:23:31.687  2024-11-18 16:23:31.399         -1 -0.463609   
26294  2024-11-18T16:23:31.687  2024-11-18 16:23:31.399         -1 -0.655035   
26295  2024-11-18T16:23:31.687  2024-11-18 16:23:31.400         -1 -0.371187   

          Acc-Y      Acc-Z  
0      3.911667   9.046964  
1      3.912265   8.876774  
2      3.915854   8.899506  
3      3.952644   8.932108  
4      3.912564   9.052647  
...         ...        ...  
26291  3.773481  10.219746  
26292  4.092325   9.563215  
26293  4.396513   8.691330  
26294  4.551747   7.945068  
26295  4.523930   8.038388  

[26296 rows x 6 columns]

In [6]:
plot_accelerometer_data(df_combined, 'E1 P1 Handlebar Accelerometer Data of Cobblestone Road')

In [ ]:
# 1. before 16:20:12
# 2. between 16:20:24 and 16:21:40
# 3. between 16:21:55 and 16:23:15

In [9]:
df_combined['NTP'] = pd.to_datetime(df_combined['NTP'])

mask = ~(
    (df_combined['NTP'] < '2024-11-18 16:20:12') |
    ((df_combined['NTP'] >= '2024-11-18 16:20:24') & (df_combined['NTP'] <= '2024-11-18 16:21:40')) |
    ((df_combined['NTP'] >= '2024-11-18 16:21:55') & (df_combined['NTP'] <= '2024-11-18 16:23:15'))
)

df_combined = df_combined[mask].reset_index(drop=True)

In [10]:
print(df_combined.shape)

(10846, 6)


In [15]:
df_combined.to_csv('../../data/RoadRoughness/Raw/Cobblestone/P1/Accelerometer_filtered.csv', index=False)

In [18]:
# Downsampling:
df = pd.read_csv('../../data/RoadRoughness/Raw/Cobblestone/P1/Accelerometer_filtered.csv')
df_selected = df[['NTP', 'Acc-X', 'Acc-Y', 'Acc-Z']].copy()
df_100hz = downsample_to_frequency(
    df_selected,
    target_hz=100,
    timestamp_col='NTP',
    output_path='../../data/RoadRoughness/Raw/Cobblestone/P1/Accelerometer_filtered_combined_100hz.csv',
    categorical_attributes=None
)
df_30hz = downsample_to_frequency(
    df_selected,
    target_hz=30,
    timestamp_col='NTP',
    output_path='../../data/RoadRoughness/Raw/Cobblestone/P1/Accelerometer_filtered_combined_30hz.csv',
    categorical_attributes=None
)

In [17]:
# plot the combined data
name = 'P3 Handlebar Accelerometer Data of 100Hz'
plot_accelerometer_data(df_100hz, name)
name = 'P3 Handlebar Accelerometer Data of 30Hz'
plot_accelerometer_data(df_30hz, name)

In [ ]:
# 100hz, divide data, 0.5s window size, 50% overlapping
df_combined_100hz = pd.read_csv('../../data/RoadRoughness/Raw/Cobblestone/P1/Accelerometer_filtered_combined_100hz.csv')
#Segmentation into 50% Overlapping
segments_100hz = segment_acceleration_data_overlapping_numpy(
    df_combined_100hz,
    window_size=50,   # 0.5s at 100Hz
    overlap=50,       # 50% overlap
    channels=['Acc-X', 'Acc-Y', 'Acc-Z'],
)
print(segments_100hz.shape)
np.savez(
    '../../data/RoadRoughness/Raw/Cobblestone/P1/segments_100hz_0.5s_50overlap.npz',
    segments = segments_100hz
)

(796, 50, 3)

In [ ]:
# 30hz, 0.5s window size, 50% overlapping
df_combined_30hz = pd.read_csv('../../data/RoadRoughness/Raw/Cobblestone/P1/Accelerometer_filtered_combined_30hz.csv')
#Segmentation into 50% Overlapping
segments = segment_acceleration_data_overlapping_numpy(
    df_combined_30hz,
    window_size=15,   # 0.5s at 30Hz
    overlap=50,       # 50% overlap
    channels=['Acc-X', 'Acc-Y', 'Acc-Z'],
)
print(segments.shape)
np.savez(
    '../../data/RoadRoughness/Raw/Cobblestone/P1/segments_30hz_0.5s_50overlap.npz',
    segments = segments
)

(862, 15, 3)


In [ ]:
# 100hz, 1s window size, 50% overlapping
df_combined_100hz = pd.read_csv('../../data/RoadRoughness/Raw/Cobblestone/P1/Accelerometer_filtered_combined_100hz.csv')
#Segmentation into 50% Overlapping
segments_100hz = segment_acceleration_data_overlapping_numpy(
    df_combined_100hz,
    window_size=100,   # 1s at 100Hz
    overlap=50,       # 50% overlap
    channels=['Acc-X', 'Acc-Y', 'Acc-Z'],
)
print(segments_100hz.shape)
np.savez(
    '../../data/RoadRoughness/Raw/Cobblestone/P1/segments_100hz_1s_50overlap.npz',
    segments = segments_100hz
)

(397, 100, 3)


In [4]:
# 30hz, 1s window size, 50% overlapping
df_combined_30hz = pd.read_csv('../../data/RoadRoughness/Raw/Cobblestone/P1/Accelerometer_filtered_combined_30hz.csv')
#Segmentation into 50% Overlapping
segments = segment_acceleration_data_overlapping_numpy(
    df_combined_30hz,
    window_size=30,   # 1s at 30Hz
    overlap=50,       # 50% overlap
    channels=['Acc-X', 'Acc-Y', 'Acc-Z'],
)
print(segments.shape)
np.savez(
    '../../data/RoadRoughness/Raw/Cobblestone/P1/segments_30hz_1s_50overlap.npz',
    segments = segments
)

(401, 30, 3)
